In [15]:
# Импортируем библиотеки
import os
import pandas as pd
import seaborn as sn
import numpy as np
import dask.dataframe as dd
import matplotlib.pyplot as plt
from sklearn.preprocessing import StandardScaler
from sklearn.cluster import KMeans
from sklearn.cluster import AgglomerativeClustering


In [16]:
df = pd.read_csv(f'data_year.csv', sep=',')
df

qw  qw_count    amount_sum   txn_id_sum       revenue  \
0              2         8  2.012325e+04    859929894      2.598750   
1              3         1  3.500000e+03    181102515      0.000000   
2              5         2  7.129745e+02    307721677      6.981590   
3              6         4  1.397550e+04    733117916    139.510000   
4              7         2  2.975000e+03    286228010      7.000000   
...          ...       ...           ...          ...           ...   
2555839  4631147       383  1.750018e+05  47095025038   1804.882012   
2555840  4631148        34  4.941300e+03   4101960613     49.250600   
2555841  4631149        41  1.419590e+04   7226124443    175.954450   
2555842  4631151         5  7.756892e+03    666220309     56.317800   
2555843  4631152       169  2.057817e+06  27082411337  23262.574650   

               costs        date  
0        -102.316250  2022-02-10  
1         -28.000000  2022-12-03  
2          -7.911160  2022-08-14  
3         -66.000000  2022-12-12  
4          -5.000000  2022-11-27  
...              ...         ...  
2555839  -778.034058  2022-11-21  
2555840   -40.814815  2022-04-13  
2555841  -153.069195  2022-12-13  
2555842   -53.791580  2022-06-29  
2555843 -5904.923563  2022-12-11  

[2555844 rows x 7 columns]

In [17]:
# Recency
day = '2022-01-01' # Начальная дата - самая ранняя
day = pd.to_datetime(day)
df['date'] =  pd.to_datetime(df['date']).dt.normalize()
dates = df['date'].to_list()
df = df.assign(date = -1 * (day - df['date'])) # Берем начальную и вычитаем из нее максимальную дату 
df['date'] = [-1*(day - date).days for date in dates]
recency = df['date']
recency

0           40
1          336
2          225
3          345
4          330
          ... 
2555839    324
2555840    102
2555841    346
2555842    179
2555843    344
Name: date, Length: 2555844, dtype: int64

In [18]:
# Frequency
freq = df['qw_count']
freq

0            8
1            1
2            2
3            4
4            2
          ... 
2555839    383
2555840     34
2555841     41
2555842      5
2555843    169
Name: qw_count, Length: 2555844, dtype: int64

In [19]:
# Monetary value

money = df['amount_sum']
money

0          2.012325e+04
1          3.500000e+03
2          7.129745e+02
3          1.397550e+04
4          2.975000e+03
               ...     
2555839    1.750018e+05
2555840    4.941300e+03
2555841    1.419590e+04
2555842    7.756892e+03
2555843    2.057817e+06
Name: amount_sum, Length: 2555844, dtype: float64

In [20]:
recency.columns=['Recency']
freq.columns=['Frequency']
money.columns=['Monetary']
RFM = pd.concat([recency, freq, money], axis=1)
RFM

date  qw_count    amount_sum
0          40         8  2.012325e+04
1         336         1  3.500000e+03
2         225         2  7.129745e+02
3         345         4  1.397550e+04
4         330         2  2.975000e+03
...       ...       ...           ...
2555839   324       383  1.750018e+05
2555840   102        34  4.941300e+03
2555841   346        41  1.419590e+04
2555842   179         5  7.756892e+03
2555843   344       169  2.057817e+06

[2555844 rows x 3 columns]

In [21]:
RFM[RFM.isnull().any(1)]

C:\Users\Xiaomi\AppData\Local\Temp\ipykernel_29080\4253055925.py:1: FutureWarning: In a future version of pandas all arguments of DataFrame.any and Series.any will be keyword-only.
  RFM[RFM.isnull().any(1)]


Empty DataFrame
Columns: [date, qw_count, amount_sum]
Index: []

In [22]:
df.dropna()

qw  qw_count    amount_sum   txn_id_sum       revenue  \
0              2         8  2.012325e+04    859929894      2.598750   
1              3         1  3.500000e+03    181102515      0.000000   
2              5         2  7.129745e+02    307721677      6.981590   
3              6         4  1.397550e+04    733117916    139.510000   
4              7         2  2.975000e+03    286228010      7.000000   
...          ...       ...           ...          ...           ...   
2555839  4631147       383  1.750018e+05  47095025038   1804.882012   
2555840  4631148        34  4.941300e+03   4101960613     49.250600   
2555841  4631149        41  1.419590e+04   7226124443    175.954450   
2555842  4631151         5  7.756892e+03    666220309     56.317800   
2555843  4631152       169  2.057817e+06  27082411337  23262.574650   

               costs  date  
0        -102.316250    40  
1         -28.000000   336  
2          -7.911160   225  
3         -66.000000   345  
4          -5.000000   330  
...              ...   ...  
2555839  -778.034058   324  
2555840   -40.814815   102  
2555841  -153.069195   346  
2555842   -53.791580   179  
2555843 -5904.923563   344  

[2555844 rows x 7 columns]

In [24]:
# Машинное обучение
scaler = StandardScaler()
scaled = scaler.fit_transform(RFM)

# Выбираем количество кластеров
# inertia = []
# for i in np.arange(1, 11):
#     kmeans = KMeans(n_clusters=i, init = 'k-means++')
#     kmeans.fit(scaled)
#     inertia.append(kmeans.inertia_)

# plt.plot(inertia, marker='o')

In [25]:
# Из графика видно, что нам нужно 3 Кластера
kmeans = KMeans(n_clusters=3)
kmeans.fit(scaled)
df['Clusters'] = (kmeans.labels_ + 1)
df

c:\Users\Xiaomi\AppData\Local\Programs\Python\Python311\Lib\site-packages\sklearn\cluster\_kmeans.py:870: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  warnings.warn(


qw  qw_count    amount_sum   txn_id_sum       revenue  \
0              2         8  2.012325e+04    859929894      2.598750   
1              3         1  3.500000e+03    181102515      0.000000   
2              5         2  7.129745e+02    307721677      6.981590   
3              6         4  1.397550e+04    733117916    139.510000   
4              7         2  2.975000e+03    286228010      7.000000   
...          ...       ...           ...          ...           ...   
2555839  4631147       383  1.750018e+05  47095025038   1804.882012   
2555840  4631148        34  4.941300e+03   4101960613     49.250600   
2555841  4631149        41  1.419590e+04   7226124443    175.954450   
2555842  4631151         5  7.756892e+03    666220309     56.317800   
2555843  4631152       169  2.057817e+06  27082411337  23262.574650   

               costs  date  Clusters  
0        -102.316250    40         3  
1         -28.000000   336         1  
2          -7.911160   225         1  
3         -66.000000   345         1  
4          -5.000000   330         1  
...              ...   ...       ...  
2555839  -778.034058   324         1  
2555840   -40.814815   102         3  
2555841  -153.069195   346         1  
2555842   -53.791580   179         3  
2555843 -5904.923563   344         1  

[2555844 rows x 8 columns]

In [26]:
df = df.drop(columns=['qw_count', 'amount_sum', 'txn_id_sum', 'revenue', 'costs', 'date'])

df.to_csv('clusters.csv')

In [ ]:
df = df.assign(average_check=df['amount_sum']/df['qw_count'])
df.to_csv('df_clusters.csv')

In [ ]:
group = df.groupby(['Clusters']).agg({
        'qw_count': 'sum',
        'amount_sum': 'sum',
        'txn_id_sum': 'sum',
        'revenue': 'sum',
        'costs': 'sum',
        'date': 'mean'
    })
group

qw_count               amount_sum         txn_id_sum  \
Clusters                                                         
1         76366657 156,038,468,673.63418579  11208689472840030   
2         11906837  28,340,992,876.83960724   1425993208177419   
3         11398452  70,640,564,683.99786377   1655093385871196   

                        revenue                 costs         date  
Clusters                                                            
1        1,444,458,328.68088770 -717,394,650.83337879 311.04602321  
2          251,648,226.00352466 -123,539,041.49623550 103.46362606  
3          777,814,724.89214826 -364,560,355.42639500 338.75460993

In [ ]:
pd.options.display.float_format ='{:,.8f}'.format
RFM['Clusters'] = (kmeans.labels_ + 1)
RFM_group = RFM.groupby(['Clusters'])['date', 'qw_count', 'amount_sum'].mean()
RFM_group

C:\Users\Xiaomi\AppData\Local\Temp\ipykernel_26256\3700519853.py:3: FutureWarning: Indexing with multiple keys (implicitly converted to a tuple of keys) will be deprecated, use a list instead.
  RFM_group = RFM.groupby(['Clusters'])['date', 'qw_count', 'amount_sum'].mean()


date       qw_count          amount_sum
Clusters                                                
1        311.04602321    55.33382677    113,062.50574131
2        103.46362606    10.17594881     24,221.08346395
3        338.75460993 2,021.00212766 12,524,922.81631168

In [ ]:
group = group.assign(average_check=group['amount_sum']/group['qw_count'])
group

qw_count               amount_sum         txn_id_sum  \
Clusters                                                         
1         76366657 156,038,468,673.63418579  11208689472840030   
2         11906837  28,340,992,876.83960724   1425993208177419   
3         11398452  70,640,564,683.99786377   1655093385871196   

                        revenue                 costs         date  \
Clusters                                                             
1        1,444,458,328.68088770 -717,394,650.83337879 311.04602321   
2          251,648,226.00352466 -123,539,041.49623550 103.46362606   
3          777,814,724.89214826 -364,560,355.42639500 338.75460993   

          average_check  
Clusters                 
1        2,043.28007541  
2        2,380.22850878  
3        6,197.38230104

In [ ]:
df

qw  qw_count         amount_sum   txn_id_sum         revenue  \
0              2         8    20,123.25000000    859929894      2.59875000   
1              3         1     3,500.00000000    181102515      0.00000000   
2              5         2       712.97450000    307721677      6.98159000   
3              6         4    13,975.50000000    733117916    139.51000000   
4              7         2     2,975.00000000    286228010      7.00000000   
...          ...       ...                ...          ...             ...   
2555839  4631147       383   175,001.82000000  47095025038  1,804.88201250   
2555840  4631148        34     4,941.30000000   4101960613     49.25060000   
2555841  4631149        41    14,195.89500000   7226124443    175.95445000   
2555842  4631151         5     7,756.89250000    666220309     56.31780000   
2555843  4631152       169 2,057,816.84500000  27082411337 23,262.57465000   

                  costs  date  Clusters   average_check  
0         -102.31625000    40         2  2,515.40625000  
1          -28.00000000   336         1  3,500.00000000  
2           -7.91116000   225         1    356.48725000  
3          -66.00000000   345         1  3,493.87500000  
4           -5.00000000   330         1  1,487.50000000  
...                 ...   ...       ...             ...  
2555839   -778.03405750   324         1    456.92381201  
2555840    -40.81481500   102         2    145.33235294  
2555841   -153.06919500   346         1    346.24134146  
2555842    -53.79158000   179         2  1,551.37850000  
2555843 -5,904.92356250   344         1 12,176.43103550  

[2555844 rows x 9 columns]

In [ ]:
quantity_users = df.groupby(['Clusters'])['qw'].count()
quantity_users

Clusters
1    1380108
2    1170096
3       5640
Name: qw, dtype: int64

In [ ]:
group['quantity_users'] = quantity_users
group

qw_count               amount_sum         txn_id_sum  \
Clusters                                                         
1         76366657 156,038,468,673.63418579  11208689472840030   
2         11906837  28,340,992,876.83960724   1425993208177419   
3         11398452  70,640,564,683.99786377   1655093385871196   

                        revenue                 costs         date  \
Clusters                                                             
1        1,444,458,328.68088770 -717,394,650.83337879 311.04602321   
2          251,648,226.00352466 -123,539,041.49623550 103.46362606   
3          777,814,724.89214826 -364,560,355.42639500 338.75460993   

          quantity_users  
Clusters                  
1                1380108  
2                1170096  
3                   5640

In [ ]:
registration = pd.read_csv(f'dataset/reg_data/qw_regs.csv', sep=';')
registration


nn_qw              from_dt              till_dt
0             10  2018-11-07 20:44:22  2000-01-01 00:00:00
1             14  2021-05-17 18:11:02  2000-01-01 00:00:00
2             74  2021-10-30 20:23:47  2000-01-01 00:00:00
3            113  2021-10-29 19:18:04  2000-01-01 00:00:00
4            166  2021-10-26 19:13:10  2022-12-31 06:14:52
...          ...                  ...                  ...
4796756  4630943  2022-07-20 14:39:55  2000-01-01 00:00:00
4796757  4630944  2022-03-06 23:35:20  2000-01-01 00:00:00
4796758  4631044  2022-03-27 11:29:19  2000-01-01 00:00:00
4796759  4631124  2022-12-04 22:15:51  2000-01-01 00:00:00
4796760  4631189  2021-08-16 16:26:52  2000-01-01 00:00:00

[4796761 rows x 3 columns]

In [ ]:
df_new_users = pd.concat([df, registration], axis=1)
df_new_users = df_new_users.dropna()
df_new_users


qw     qw_count         amount_sum  \
0               2.00000000   8.00000000    20,123.25000000   
1               3.00000000   1.00000000     3,500.00000000   
2               5.00000000   2.00000000       712.97450000   
3               6.00000000   4.00000000    13,975.50000000   
4               7.00000000   2.00000000     2,975.00000000   
...                    ...          ...                ...   
2555839 4,631,147.00000000 383.00000000   175,001.82000000   
2555840 4,631,148.00000000  34.00000000     4,941.30000000   
2555841 4,631,149.00000000  41.00000000    14,195.89500000   
2555842 4,631,151.00000000   5.00000000     7,756.89250000   
2555843 4,631,152.00000000 169.00000000 2,057,816.84500000   

                     txn_id_sum         revenue           costs         date  \
0          859,929,894.00000000      2.59875000   -102.31625000  40.00000000   
1          181,102,515.00000000      0.00000000    -28.00000000 336.00000000   
2          307,721,677.00000000      6.98159000     -7.91116000 225.00000000   
3          733,117,916.00000000    139.51000000    -66.00000000 345.00000000   
4          286,228,010.00000000      7.00000000     -5.00000000 330.00000000   
...                         ...             ...             ...          ...   
2555839 47,095,025,038.00000000  1,804.88201250   -778.03405750 324.00000000   
2555840  4,101,960,613.00000000     49.25060000    -40.81481500 102.00000000   
2555841  7,226,124,443.00000000    175.95445000   -153.06919500 346.00000000   
2555842    666,220,309.00000000     56.31780000    -53.79158000 179.00000000   
2555843 27,082,411,337.00000000 23,262.57465000 -5,904.92356250 344.00000000   

          Clusters   average_check    nn_qw              from_dt  \
0       2.00000000  2,515.40625000       10  2018-11-07 20:44:22   
1       1.00000000  3,500.00000000       14  2021-05-17 18:11:02   
2       1.00000000    356.48725000       74  2021-10-30 20:23:47   
3       1.00000000  3,493.87500000      113  2021-10-29 19:18:04   
4       1.00000000  1,487.50000000      166  2021-10-26 19:13:10   
...            ...             ...      ...                  ...   
2555839 1.00000000    456.92381201  1432096  2022-10-26 14:39:15   
2555840 2.00000000    145.33235294  1432111  2022-05-12 13:22:17   
2555841 1.00000000    346.24134146  1432139  2022-06-02 11:36:34   
2555842 2.00000000  1,551.37850000  1432184  2021-05-15 23:04:38   
2555843 1.00000000 12,176.43103550  1432203  2022-05-29 13:41:32   

                     till_dt  
0        2000-01-01 00:00:00  
1        2000-01-01 00:00:00  
2        2000-01-01 00:00:00  
3        2000-01-01 00:00:00  
4        2022-12-31 06:14:52  
...                      ...  
2555839  2000-01-01 00:00:00  
2555840  2000-01-01 00:00:00  
2555841  2000-01-01 00:00:00  
2555842  2000-01-01 00:00:00  
2555843  2000-01-01 00:00:00  

[2555844 rows x 12 columns]

In [ ]:
df_new_users['from_dt'] = pd.to_datetime(df_new_users['from_dt']).dt.normalize()
dates_reg = df_new_users['from_dt'].to_list()
day = pd.to_datetime('2022-01-01')
spisok = []
for d in dates_reg:
    if (day - d).days > 0:
        spisok.append(0)
    else:
        spisok.append(1)

print(spisok)


[0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 1, 1, 0, 0, 0, 0, 1, 0, 0, 1, 0, 0, 0, 1, 0, 0, 1, 0, 0, 1, 0, 0, 1, 1, 0, 0, 1, 0, 1, 0, 0, 0, 1, 0, 1, 0, 0, 0, 1, 0, 1, 0, 1, 0, 0, 0, 1, 1, 1, 0, 0, 1, 0, 1, 0, 0, 0, 1, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 1, 1, 1, 1, 0, 1, 0, 1, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 1, 1, 0, 0, 1, 1, 0, 0, 0, 1, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 1, 0, 1, 0, 0, 0, 0, 0, 1, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 0, 1, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 1, 0, 0, 1, 0, 1, 0, 0, 0, 1, 1, 0, 1, 1, 0, 1, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 1, 1, 0, 0, 0, 1, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 1, 0, 1, 0, 0, 1, 0, 0, 0, 0, 1, 0, 1, 0, 1, 1, 1, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 1, 0, 1, 0, 0, 0, 0, 

In [ ]:
df_new_users['is_new'] = spisok
df_new_users

qw     qw_count         amount_sum  \
0               2.00000000   8.00000000    20,123.25000000   
1               3.00000000   1.00000000     3,500.00000000   
2               5.00000000   2.00000000       712.97450000   
3               6.00000000   4.00000000    13,975.50000000   
4               7.00000000   2.00000000     2,975.00000000   
...                    ...          ...                ...   
2555839 4,631,147.00000000 383.00000000   175,001.82000000   
2555840 4,631,148.00000000  34.00000000     4,941.30000000   
2555841 4,631,149.00000000  41.00000000    14,195.89500000   
2555842 4,631,151.00000000   5.00000000     7,756.89250000   
2555843 4,631,152.00000000 169.00000000 2,057,816.84500000   

                     txn_id_sum         revenue           costs         date  \
0          859,929,894.00000000      2.59875000   -102.31625000  40.00000000   
1          181,102,515.00000000      0.00000000    -28.00000000 336.00000000   
2          307,721,677.00000000      6.98159000     -7.91116000 225.00000000   
3          733,117,916.00000000    139.51000000    -66.00000000 345.00000000   
4          286,228,010.00000000      7.00000000     -5.00000000 330.00000000   
...                         ...             ...             ...          ...   
2555839 47,095,025,038.00000000  1,804.88201250   -778.03405750 324.00000000   
2555840  4,101,960,613.00000000     49.25060000    -40.81481500 102.00000000   
2555841  7,226,124,443.00000000    175.95445000   -153.06919500 346.00000000   
2555842    666,220,309.00000000     56.31780000    -53.79158000 179.00000000   
2555843 27,082,411,337.00000000 23,262.57465000 -5,904.92356250 344.00000000   

          Clusters   average_check    nn_qw    from_dt              till_dt  \
0       2.00000000  2,515.40625000       10 2018-11-07  2000-01-01 00:00:00   
1       1.00000000  3,500.00000000       14 2021-05-17  2000-01-01 00:00:00   
2       1.00000000    356.48725000       74 2021-10-30  2000-01-01 00:00:00   
3       1.00000000  3,493.87500000      113 2021-10-29  2000-01-01 00:00:00   
4       1.00000000  1,487.50000000      166 2021-10-26  2022-12-31 06:14:52   
...            ...             ...      ...        ...                  ...   
2555839 1.00000000    456.92381201  1432096 2022-10-26  2000-01-01 00:00:00   
2555840 2.00000000    145.33235294  1432111 2022-05-12  2000-01-01 00:00:00   
2555841 1.00000000    346.24134146  1432139 2022-06-02  2000-01-01 00:00:00   
2555842 2.00000000  1,551.37850000  1432184 2021-05-15  2000-01-01 00:00:00   
2555843 1.00000000 12,176.43103550  1432203 2022-05-29  2000-01-01 00:00:00   

         is_new  
0             0  
1             0  
2             0  
3             0  
4             0  
...         ...  
2555839       1  
2555840       1  
2555841       1  
2555842       0  
2555843       1  

[2555844 rows x 13 columns]

In [ ]:
df_new_users_group = df_new_users.groupby(['Clusters']).agg({
        'qw_count': 'sum',
        'amount_sum': 'sum',
        'txn_id_sum': 'sum',
        'revenue': 'sum',
        'costs': 'sum',
        'average_check': 'mean',
        'date': 'mean',
        'is_new': 'sum'
    })
df_new_users_group['quantity_users'] = quantity_users
df_new_users_group

qw_count               amount_sum  \
Clusters                                                  
1.00000000 76,366,657.00000000 156,038,468,673.63418579   
2.00000000 11,906,837.00000000  28,340,992,876.83960724   
3.00000000 11,398,452.00000000  70,640,564,683.99786377   

                                txn_id_sum                revenue  \
Clusters                                                            
1.00000000 11,208,689,472,840,030.00000000 1,444,458,328.68088770   
2.00000000  1,425,993,208,177,419.00000000   251,648,226.00352466   
3.00000000  1,655,093,385,871,196.00000000   777,814,724.89214826   

                           costs   average_check         date  is_new  \
Clusters                                                                
1.00000000 -717,394,650.83337879  2,184.67924074 311.04602321  519524   
2.00000000 -123,539,041.49623550  2,033.63594331 103.46362606  439543   
3.00000000 -364,560,355.42639500 16,246.43580173 338.75460993    2107   

            quantity_users  
Clusters                    
1.00000000         1380108  
2.00000000         1170096  
3.00000000            5640